In [1]:
import sys
sys.path.insert(0, '..')
import numpy as np
import qutip as qt
import src
from src import (utils, paulialg, stabilizer, circuit)

# Methods for stabilizer states

## Measurement

`StabilizerState.measure(obs)` measure the stabilizer state on a set of commuting observables.

**Parameters:**
* `obs` - Observables to measure. The following types are supported:
    * `PauliList` - a list of Pauli operators (user must ensure that operators in the list are commuting, otherwise they can not measured simutaneously).
    * `StabilizerState` - stabilizers of a stabilizer state is always commuting, which can be treated as commuting observables for measurement.

**Returns:**
* `out` - measuremnt outcome, can only be $0$, $1$ for independent Pauli observables on stabilizer state, where 0 means positive (+1) eigenvalue, and 1 means negative (-1) eigenvalue.
* `log2prob` - the log2 of the probability of realizing this particular outcome.

In [3]:
state = stabilizer.ghz_state(3)
state

StabilizerState(
   +ZZI
   +IZZ
   +XXX)

In [4]:
state.measure(paulialg.paulis('ZII','IZI','IIZ'))

(array([1, 1, 1]), -1.0)

In the above example, I created a GHZ state, and did single qubit Z-basis measurements on each of the qubit. We get -1 for all qubits with probility $2^{-1}=0.5$

<div class="alert alert-block alert-danger">
Measurement will <b>in place </b> change the state, as measurement will collapse the quantum state.
</div>

In [5]:
state = stabilizer.ghz_state(3)
state.measure(paulialg.paulis('ZII','IZI','IIZ'))

(array([0, 0, 0]), -1.0)

In [6]:
state.measure(paulialg.paulis('ZII','IZI','IIZ'))

(array([0, 0, 0]), 0.0)

We see the second measurement will return the same measurement result with 100% probability

## Expectation

`StabilizerState.expect()` provide fast algorithm to evaluate expectation value of:
- Pauli operator
- Pauli Monomial/Polynomial
- Overlap between stabilizer states <font color='red'>Warning: currently it only supports pure state overlap with general stabilizer states.</font>

In [10]:
state = stabilizer.ghz_state(5)

In [11]:
state.expect(paulialg.paulis('XXXXX','IZIII','-ZZIII'))

array([ 1,  0, -1])

In [12]:
pauli_poly = 0.5*paulialg.pauli('XXXXX')+0.2j*paulialg.pauli('-ZZIII')

In [13]:
state.expect(pauli_poly)

(0.5-0.2j)

## Overlap between two stabilizer states (fidelity)

In [15]:
state = stabilizer.ghz_state(3)
state2 = stabilizer.random_clifford_state(3)
print("State overlap is:", state.expect(state2))

State overlap is: 0.25


In [16]:
tate = stabilizer.ghz_state(3)
state2 = stabilizer.random_clifford_state(3)
state2.set_r(1)
print("State overlap is:", state.expect(state2))

State overlap is: 0.125


## The probability of getting a bit-string readout (Bit-string probability)

`StabilizerState.get_prob(bitstring)` will return the probability of measuring given bitstring at current stabilizer state.
**Input**
- bitstring: Integer type 1D array
**Output**
- probability

In [17]:
state = stabilizer.ghz_state(625)

In [18]:
state.get_prob(np.ones(625))

0.5

## Transform stabilzier state by rotation/Clifford transformation

As a derived class of `PauliList`, `StabilizerState` also support `StabilizerState.rotate_by(pauli)` and `StabilizerState.transform_by(clifford_map)`

In [19]:
rho = stabilizer.ghz_state(4)

In [20]:
rho.rotate_by(paulialg.pauli([1,3,1,0]))

StabilizerState(
   -YIXI
   -XIYI
   -XZYZ
   +IYIX)

In [21]:
rho.transform_by(stabilizer.random_clifford_map(4))

StabilizerState(
   +XZYY
   +XXIZ
   +ZXIY
   -IYIX)

## Sample stabilizers from the stabilizer group

`Stabilizer.sample(L)` will sample $L$ stabilizers in the stabilizer group

In [22]:
rho = stabilizer.ghz_state(4)
rho.sample(4)

 -XYXY
 -YXXY
 -YXXY
 -XXYY

## Get density matrix of a stabilizer state

@property `StabilizerState.density_matrix` will return density matrix of stabilizer state as `PauliPolynomial`

In [24]:
stabilizer.ghz_state(2).density_matrix

0.25000 II +0.25000 XX +0.25000 ZZ -0.25000 YY

## Calculate Entropy of a stabilizer state

`StabilizerState.entropy(subsys)` will calculate the second Renyi entropy of the stabilizer state on subregion.
**Parameter**
- `subsys`: List containing the location of region

In [25]:
state = stabilizer.random_clifford_state(20)

In [26]:
state.entropy([1,5,10])

3

## Copy a stabilizer state

`StabilizerState.copy()` returns a copy of the state, such that the original state will not be touch by modification on the copy state. It is useful to copy the state for measurement (as measurement changes the state).

Example:

In [27]:
state = stabilizer.random_clifford_state(4).copy()